In [1]:
import pandas as pd
import os
from datetime import datetime, timedelta
from glob import glob

In [2]:
from tqdm import tqdm # Progress bar
tqdm.pandas()

In [3]:
flight_folder = "D:/STAT628m3/flight_processed"
climate_folders = ['D:/STAT628m3/climate2018', 'D:/STAT628m3/climate2019', 'D:/STAT628m3/climate2020', 
                   'D:/STAT628m3/climate2021', 'D:/STAT628m3/climate2022', 'D:/STAT628m3/climate2023',
                   'D:/STAT628m3/climate2024']
output_folder = 'D:/STAT628m3'
# output_folder_extracted = 'D:/STAT628m3/extracted_data'
# output_folder_merged = 'D:/STAT628m3/merged_data'
# output_file = 'D:/STAT628m3/flight_with_weather.csv'
# station_mapping_file = "D:/STAT628m3/Station_final_match.csv"

In [4]:
if not os.path.exists(output_folder):
    os.makedirs(output_folder)

In [5]:
flight_columns = [
    "FlightDate","Year", "Month",
    "DayofMonth", "DayOfWeek", "Operating_Airline ",
    "Origin", "Dest", "CRSDepTime", "DepTime", 
    "DepDelay","DepTimeBlk", "CRSArrTime", "ArrTime", "ArrDelay", "ArrTimeBlk", "Cancelled", 
    "CancellationCode", "Diverted", "CRSElapsedTime", 
    "ActualElapsedTime", "Distance", "WeatherDelay",
    # new added col for merging
    "CRSDepDatetime", "CRSDepTime_CST", "DepTime_CST", "ArrTime_CST", "CRSArrTime_CST"
]

climate_columns = [
    'DATE', 'REPORT_TYPE', 'SOURCE', 'HourlyAltimeterSetting', 'HourlyDewPointTemperature', 
    'HourlyDryBulbTemperature', 'HourlyPrecipitation', 'HourlyPresentWeatherType', 'HourlyPressureChange',
    'HourlyPressureTendency', 'HourlyRelativeHumidity', 'HourlySkyConditions', 'HourlySeaLevelPressure',
    'HourlyStationPressure', 'HourlyVisibility', 'HourlyWetBulbTemperature', 'HourlyWindDirection',
    'HourlyWindGustSpeed', 'HourlyWindSpeed'
]

In [6]:
flight_data = pd.read_csv('D:/STAT628m3/flight_data.csv')

In [7]:
flight_data.head(2)

FlightDate  Year  Month  DayofMonth  DayOfWeek Operating_Airline  Origin  \
0  2018-01-01  2018      1           1          1                 EV    ATL   
1  2018-01-02  2018      1           2          2                 EV    ATL   

  Dest  CRSDepTime DepTime  ...  Diverted CRSElapsedTime  ActualElapsedTime  \
0  ABE        1505    1703  ...         0          125.0              117.0   
1  ABE        1505    1530  ...         0          125.0              113.0   

  Distance  WeatherDelay        CRSDepDatetime        CRSDepTime_CST  \
0      692           0.0  2018-01-01T15:05:00Z  2018-01-01T20:05:00Z   
1      692           NaN  2018-01-02T15:05:00Z  2018-01-02T20:05:00Z   

            DepTime_CST           ArrTime_CST        CRSArrTime_CST  
0  2018-01-01T22:03:00Z  2018-01-02T00:00:00Z  2018-01-01T22:10:00Z  
1  2018-01-02T20:30:00Z  2018-01-02T22:23:00Z  2018-01-02T22:10:00Z  

[2 rows x 28 columns]

In [8]:
flight_data.shape

(11470108, 28)

In [9]:
flight_data.columns

Index(['FlightDate', 'Year', 'Month', 'DayofMonth', 'DayOfWeek',
       'Operating_Airline ', 'Origin', 'Dest', 'CRSDepTime', 'DepTime',
       'DepDelay', 'DepTimeBlk', 'CRSArrTime', 'ArrTime', 'ArrDelay',
       'ArrTimeBlk', 'Cancelled', 'CancellationCode', 'Diverted',
       'CRSElapsedTime', 'ActualElapsedTime', 'Distance', 'WeatherDelay',
       'CRSDepDatetime', 'CRSDepTime_CST', 'DepTime_CST', 'ArrTime_CST',
       'CRSArrTime_CST'],
      dtype='object')

In [15]:
climate_data_cache = {}

def load_climate_data(year, airport_code):
    climate_file_pattern = f"D:/STAT628m3/climate{year}/LCD_{airport_code}_{year}.csv"
    try:
        climate_data = pd.read_csv(climate_file_pattern)
        climate_data['DATE'] = pd.to_datetime(climate_data['DATE'])
        return climate_data
    except FileNotFoundError:
        print(f"File not found: {climate_file_pattern}")
        return None

In [16]:
def get_climate_data(year, airport_code):

    key = (year, airport_code)
    if key not in climate_data_cache:
        
        climate_data = load_climate_data(year, airport_code)
        climate_data_cache[key] = climate_data
    return climate_data_cache[key]

In [19]:
def find_nearest_weather(row, airport_type, time_col):
    year = row['Year']
    airport_code = row[airport_type]
    crs_dep_datetime = pd.to_datetime(row[time_col]).tz_localize(None)  # remove time zone

    # get climate data
    climate_data = get_climate_data(year, airport_code)
    if climate_data is None:
        return pd.DataFrame([[None] * len(climate_columns[1:])], columns=climate_columns[1:])

    # Process date and time in weather data
    climate_data['DATE'] = pd.to_datetime(climate_data['DATE'])
    
    # Sift through weather records prior to the time of flight
    climate_data = climate_data[climate_data['DATE'] < crs_dep_datetime]

    # Check for weather data that matches the criteria
    if climate_data.empty:
        print(f"No weather data found for {airport_code} on {crs_dep_datetime}")
        return pd.Series([None] * len(climate_columns[1:]), index=climate_columns[1:])

    # Find the closest time
    closest_row = climate_data.iloc[(crs_dep_datetime - climate_data['DATE']).abs().argsort()[:1]]
    
    # return closest_row.squeeze()[climate_columns[1:]]
    return closest_row.iloc[0][climate_columns[1:]].copy()

In [41]:
# Set chunk size and output file path
chunk_size = 100
output_file = 'D:/STAT628m3/flight_with_weather1.csv'

# Initialize the output file with headers
first_chunk = True

# Process data in chunks
for start_idx in tqdm(range(2625100, 2800001, chunk_size)):
    end_idx = min(start_idx + chunk_size, 2800001)
    
    # Slice the chunk of data
    flight_chunk = flight_data.iloc[start_idx:end_idx]
    
    # Apply the weather data function for both Origin and Dest
    origin_weather = flight_chunk.progress_apply(lambda row: find_nearest_weather(row, 'Origin', 'CRSDepTime_CST'), axis=1)
    dest_weather = flight_chunk.progress_apply(lambda row: find_nearest_weather(row, 'Dest', 'CRSDepTime_CST'), axis=1)
    
    # If the result is a Series instead of a DataFrame, make sure the result is correctly converted to a DataFrame
    if isinstance(origin_weather, pd.Series):
        origin_weather = pd.DataFrame(origin_weather.tolist(), columns=[f'Origin_{col}' for col in climate_columns[1:]])

    if isinstance(dest_weather, pd.Series):
        dest_weather = pd.DataFrame(dest_weather.tolist(), columns=[f'Dest_{col}' for col in climate_columns[1:]])
    
    
    # Rename the columns
    origin_weather.columns = [f'Origin_{col}' for col in climate_columns[1:]]
    dest_weather.columns = [f'Dest_{col}' for col in climate_columns[1:]]
    
    # Join the weather data with the current chunk
    flight_with_weather_chunk = flight_chunk.join(origin_weather).join(dest_weather)
    
    # Append to the CSV file
    flight_with_weather_chunk.to_csv(output_file, mode='a', header=first_chunk, index=False)
    
    # Set header to False after the first write
    first_chunk = False
    
    print(start_idx) # finished chunk
    print(end_idx)

100%|███████████████████████████████████████████████████████████████████████████████| 100/100 [00:00<00:00, 180.48it/s]

  0%|                                                                                 | 1/1750 [00:01<29:52,  1.02s/it]

2625100
2625200



100%|███████████████████████████████████████████████████████████████████████████████| 100/100 [00:00<00:00, 183.12it/s]

  0%|                                                                                 | 2/1750 [00:02<30:06,  1.03s/it]

2625200
2625300



100%|███████████████████████████████████████████████████████████████████████████████| 100/100 [00:00<00:00, 222.23it/s]

  0%|▏                                                                                | 3/1750 [00:03<33:29,  1.15s/it]

...

2799800
2799900



100%|███████████████████████████████████████████████████████████████████████████████| 100/100 [00:00<00:00, 151.13it/s]

100%|█████████████████████████████████████████████████████████████████████████████▉| 1749/1750 [33:18<00:01,  1.24s/it]

2799900
2800000



100%|███████████████████████████████████████████████████████████████████████████████████| 1/1 [00:00<00:00, 494.32it/s]

100%|██████████████████████████████████████████████████████████████████████████████| 1750/1750 [33:18<00:00,  1.14s/it]

2800000
2800001


In [43]:
pd.read_csv(output_file).shape

C:\Users\zhixi\AppData\Local\Temp\ipykernel_5788\1126822712.py:1: DtypeWarning: Columns (1,2,3,4,8,10,12,14,16,18,19,20,21,22,29,30,31,32,35,36,37,39,40,41,42,44,45,47,48,49,50,51,52,53,54,55,56,57,58,59,60,61,62,63) have mixed types. Specify dtype option on import or set low_memory=False.
  pd.read_csv(output_file).shape


(2798511, 64)

# Below are drafts!

下面这个block每个人跑一部分   
wyd 1-2800000   
xyc 2800001-5600000   
mario 5600001-8400000   
tutu 8400001-11470108   
把存的文件改成1 2 3 4！！！

In [15]:
# 为每行添加Origin和Dest的气象数据
origin_weather = flight_data.head(280).progress_apply(lambda row: find_nearest_weather(row, 'Origin', 'CRSDepTime_CST'), axis=1)
# dest_weather = flight_data.head(2800000).progress_apply(lambda row: find_nearest_weather(row, 'Dest', 'CRSDepTime_CST'), axis=1)

100%|███████████████████████████████████████████████████████████████████████████████| 280/280 [00:01<00:00, 193.94it/s]


In [16]:
# 重命名 origin_weather 的列名
origin_weather.columns = [f'Origin_{col}' for col in climate_columns[1:]]

# 重命名 dest_weather 的列名
# dest_weather.columns = [f'Dest_{col}' for col in climate_columns[1:]]

In [19]:
pd.DataFrame([[None] * len(climate_columns[1:])], columns=climate_columns[1:])

REPORT_TYPE SOURCE HourlyAltimeterSetting HourlyDewPointTemperature  \
0        None   None                   None                      None   

  HourlyDryBulbTemperature HourlyPrecipitation HourlyPresentWeatherType  \
0                     None                None                     None   

  HourlyPressureChange HourlyPressureTendency HourlyRelativeHumidity  \
0                 None                   None                   None   

  HourlySkyConditions HourlySeaLevelPressure HourlyStationPressure  \
0                None                   None                  None   

  HourlyVisibility HourlyWetBulbTemperature HourlyWindDirection  \
0             None                     None                None   

  HourlyWindGustSpeed HourlyWindSpeed  
0                None            None

In [20]:
origin_weather.columns

Index(['Origin_REPORT_TYPE', 'Origin_SOURCE', 'Origin_HourlyAltimeterSetting',
       'Origin_HourlyDewPointTemperature', 'Origin_HourlyDryBulbTemperature',
       'Origin_HourlyPrecipitation', 'Origin_HourlyPresentWeatherType',
       'Origin_HourlyPressureChange', 'Origin_HourlyPressureTendency',
       'Origin_HourlyRelativeHumidity', 'Origin_HourlySkyConditions',
       'Origin_HourlySeaLevelPressure', 'Origin_HourlyStationPressure',
       'Origin_HourlyVisibility', 'Origin_HourlyWetBulbTemperature',
       'Origin_HourlyWindDirection', 'Origin_HourlyWindGustSpeed',
       'Origin_HourlyWindSpeed'],
      dtype='object')

In [17]:
flight_with_weather1 = flight_data.head(2800000).join(origin_weather)

KeyboardInterrupt: 

In [ ]:
flight_with_weather1.columns

In [ ]:
# 写入文件
flight_with_weather1.to_csv('D:/STAT628m3/flight_with_weather1.csv', index=False)

In [ ]:
dest_weather = flight_data.head(2800000).progress_apply(lambda row: find_nearest_weather(row, 'Dest', 'CRSDepTime_CST'), axis=1)

In [ ]:
# 重命名 dest_weather 的列名
dest_weather.columns = [f'Dest_{col}' for col in climate_columns[1:]]

In [ ]:
flight_with_weather11 = flight_with_weather1.head(2800000).join(dest_weather)

In [ ]:
flight_with_weather11.columns

In [ ]:
# 写入文件
flight_with_weather11.to_csv('D:/STAT628m3/flight_with_weather1.csv', index=False)